In [ ]:
from modelscope.msdatasets import MsDataset
split = "test"
split = "validation"
ds =  MsDataset.load('AI-ModelScope/ScienceQA', subset_name='default', split=split)


In [3]:
# ds[:3]

In [2]:
info = ds.info
# info?
from dataclasses import asdict

info_dict = asdict(info)
# info_dict


In [5]:
# Add a new column named "index".
# We'll create a 1-based index to match the target format's requirement.
ds = ds.add_column("index", range(1, len(ds) + 1))

# You can verify the result by checking the first record:
print(ds[0])

{'image': None, 'question': "What does the verbal irony in this text suggest?\nAccording to Mr. Herrera's kids, his snoring is as quiet as a jackhammer.", 'choices': ['The snoring is loud.', 'The snoring occurs in bursts.'], 'answer': 0, 'hint': '', 'task': 'closed choice', 'grade': 'grade8', 'subject': 'language science', 'topic': 'figurative-language', 'category': 'Literary devices', 'skill': 'Interpret figures of speech', 'lecture': 'Figures of speech are words or phrases that use language in a nonliteral or unusual way. They can make writing more expressive.\nVerbal irony involves saying one thing but implying something very different. People often use verbal irony when they are being sarcastic.\nOlivia seems thrilled that her car keeps breaking down.\nEach breakdown is as enjoyable as a punch to the face.', 'solution': "The text uses verbal irony, which involves saying one thing but implying something very different.\nAs quiet as a jackhammer suggests that the snoring is loud. A j

In [4]:
ds = ds.add_column('split', [split] * len(ds))
print(ds[0])


{'image': None, 'question': "What does the verbal irony in this text suggest?\nAccording to Mr. Herrera's kids, his snoring is as quiet as a jackhammer.", 'choices': ['The snoring is loud.', 'The snoring occurs in bursts.'], 'answer': 0, 'hint': '', 'task': 'closed choice', 'grade': 'grade8', 'subject': 'language science', 'topic': 'figurative-language', 'category': 'Literary devices', 'skill': 'Interpret figures of speech', 'lecture': 'Figures of speech are words or phrases that use language in a nonliteral or unusual way. They can make writing more expressive.\nVerbal irony involves saying one thing but implying something very different. People often use verbal irony when they are being sarcastic.\nOlivia seems thrilled that her car keeps breaking down.\nEach breakdown is as enjoyable as a punch to the face.', 'solution': "The text uses verbal irony, which involves saying one thing but implying something very different.\nAs quiet as a jackhammer suggests that the snoring is loud. A j

处理 Image 变成 base64 字符串

In [6]:
ds = ds.rename_column("image", "image_pil")

In [7]:
from vlmeval.smp.vlm import encode_image_to_base64

# 1. Define a function to process one record
def encode_image(example):
    try:
        # The 'image' field might be None for some examples
        image = None
        if example['image_pil'] is not None:
            # Apply the encoding function to the image in the record
            image = encode_image_to_base64(example['image_pil'], fmt='PNG')
        example['image2'] = image
        return example
    except Exception as e:
        print(f"Error encoding image: {e}")
        print("stucked at example: ", example)
        example['image2'] = None
        return example

# 2. Apply this function to every record in the dataset
ds = ds.map(encode_image, batched=False)

Map:   0%|          | 0/4241 [00:00<?, ? examples/s]

In [8]:
ds = ds.rename_column("image2", "image")

把 answer 变成 ABCD

In [9]:
abcde = ['A', 'B', 'C', 'D', 'E']
ds = ds.map(lambda x: {'answer': abcde[x['answer']]})


Map:   0%|          | 0/4241 [00:00<?, ? examples/s]

question, hint，task，grade，subject，topic，category，skill，lecture，solution都有了

In [10]:
ds[1]


{'image_pil': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=202x202>,
 'question': "Which animal's mouth is also adapted for bottom feeding?",
 'choices': ['discus', 'armored catfish'],
 'answer': 'B',
 'hint': "Sturgeons eat invertebrates, plants, and small fish. They are bottom feeders. Bottom feeders find their food at the bottom of rivers, lakes, and the ocean.\nThe 's mouth is located on the underside of its head and points downward. Its mouth is adapted for bottom feeding.\nFigure: sturgeon.",
 'task': 'closed choice',
 'grade': 'grade3',
 'subject': 'natural science',
 'topic': 'biology',
 'category': 'Adaptations',
 'skill': 'Animal adaptations: beaks, mouths, and necks',
 'lecture': "An adaptation is an inherited trait that helps an organism survive or reproduce. Adaptations can include both body parts and behaviors.\nThe shape of an animal's mouth is one example of an adaptation. Animals' mouths can be adapted in different ways. For example, a large mouth with sharp te

现在把 choices 列表，展开为 A, B, C, D, E 五个列

In [11]:
abcde = ['A', 'B', 'C', 'D', 'E']
def expand_choices(row):
    choices = row['choices']
    # 这是个大坑，本质上arrow是列数据集，而不是行数据集，所以如果不显式的设置新列会报错
    # for i, choice in enumerate(choices):
    #     row[abcde[i]] = choice
    length = len(choices)
    for i, choice in enumerate(abcde):
        if i < length:
            row[choice] = choices[i]
        else:
            row[choice] = None
    return row
ds = ds.map(expand_choices)

Map:   0%|          | 0/4241 [00:00<?, ? examples/s]

In [12]:
ds[1]

{'image_pil': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=202x202>,
 'question': "Which animal's mouth is also adapted for bottom feeding?",
 'choices': ['discus', 'armored catfish'],
 'answer': 'B',
 'hint': "Sturgeons eat invertebrates, plants, and small fish. They are bottom feeders. Bottom feeders find their food at the bottom of rivers, lakes, and the ocean.\nThe 's mouth is located on the underside of its head and points downward. Its mouth is adapted for bottom feeding.\nFigure: sturgeon.",
 'task': 'closed choice',
 'grade': 'grade3',
 'subject': 'natural science',
 'topic': 'biology',
 'category': 'Adaptations',
 'skill': 'Animal adaptations: beaks, mouths, and necks',
 'lecture': "An adaptation is an inherited trait that helps an organism survive or reproduce. Adaptations can include both body parts and behaviors.\nThe shape of an animal's mouth is one example of an adaptation. Animals' mouths can be adapted in different ways. For example, a large mouth with sharp te

In [13]:
len(ds)

4241

In [14]:
ds = ds.remove_columns(['image_pil'])

In [15]:
import os
import pandas as pd

In [16]:
df = ds.to_pandas()
df

question  \
0     What does the verbal irony in this text sugges...   
1     Which animal's mouth is also adapted for botto...   
2     Is this a sentence fragment?\nDuring the const...   
3       Which of the following could Wendy's test show?   
4            Which correctly shows the title of a play?   
...                                                 ...   
4236  Compare the motion of two fish. Which fish was...   
4237  Using only these supplies, which question can ...   
4238                    Which continent is highlighted?   
4239  What kind of sentence is this?\nGive Daniel a ...   
4240  What information supports the conclusion that ...   

                                                choices answer  \
0     [The snoring is loud., The snoring occurs in b...      A   
1                             [discus, armored catfish]      B   
2                                             [no, yes]      B   
3     [whether producing more insulin would help the...      C   
4        [A breath of Fresh Air, A Breath of Fresh Air]      B   
...                                                 ...    ...   
4236  [a fish that moved 20kilometers in 5hours, a f...      A   
4237  [Do the squirrels select sunflower seeds or wa...      A   
4238     [South America, North America, Europe, Africa]      C   
4239           [exclamatory, interrogative, imperative]      C   
4240  [Rick's coworker also has curly hair., Rick's ...      B   

                                                   hint           task  \
0                                                        closed choice   
1     Sturgeons eat invertebrates, plants, and small...  closed choice   
2                                                            yes or no   
3     People can use the engineering-design process ...  closed choice   
4                                                        closed choice   
...                                                 ...            ...   
4236                                                     closed choice   
4237  Garrett enjoys feeding the squirrels in his ba...  closed choice   
4238                                                     closed choice   
4239                                                     closed choice   
4240  Read the description of a trait.\nRick has cur...  closed choice   

        grade           subject                              topic  \
0      grade8  language science                figurative-language   
1      grade3   natural science                            biology   
2     grade12  language science                 writing-strategies   
3      grade7   natural science  science-and-engineering-practices   
4      grade3  language science                     capitalization   
...       ...               ...                                ...   
4236   grade2   natural science                            physics   
4237   grade7   natural science  science-and-engineering-practices   
4238   grade8    social science                          geography   
4239   grade6  language science                        punctuation   
4240   grade7   natural science                            biology   

                               category  \
0                      Literary devices   
1                           Adaptations   
2     Sentences, fragments, and run-ons   
3                 Engineering practices   
4                            Formatting   
...                                 ...   
4236                   Force and motion   
4237              Designing experiments   
4238                 Physical Geography   
4239  Sentences, fragments, and run-ons   
4240                    Genes to traits   

                                                  skill  \
0                           Interpret figures of speech   
1          Animal adaptations: beaks, mouths, and necks   
2                           Identify sentence fragments   
3        Evaluate tests of engineering-design solutions   
4  

In [18]:
df.to_csv(f'data/ScienceQA_{split}-fixed.tsv', index=False, sep='\t')


In [19]:
import json
info_dict = asdict(ds.info)
json.dump(info_dict, open(f'info-default-{split}.json', 'w'), ensure_ascii=False, indent=2)